<h1>Table of Contents<span class="tocSkip"></span></h1>
<div class="toc"><ul class="toc-item"><li><span><a href="#Optimization" data-toc-modified-id="Optimization-1"><span class="toc-item-num">1&nbsp;&nbsp;</span>Optimization</a></span><ul class="toc-item"><li><span><a href="#Setup" data-toc-modified-id="Setup-1.1"><span class="toc-item-num">1.1&nbsp;&nbsp;</span>Setup</a></span></li><li><span><a href="#Single-Task-Optimization-A" data-toc-modified-id="Single-Task-Optimization-A-1.2"><span class="toc-item-num">1.2&nbsp;&nbsp;</span>Single Task Optimization A</a></span><ul class="toc-item"><li><span><a href="#Generate-Suggestions" data-toc-modified-id="Generate-Suggestions-1.2.1"><span class="toc-item-num">1.2.1&nbsp;&nbsp;</span>Generate Suggestions</a></span></li></ul></li><li><span><a href="#Multitask-Experiments-B" data-toc-modified-id="Multitask-Experiments-B-1.3"><span class="toc-item-num">1.3&nbsp;&nbsp;</span>Multitask Experiments B</a></span><ul class="toc-item"><li><span><a href="#Generate-Suggestions" data-toc-modified-id="Generate-Suggestions-1.3.1"><span class="toc-item-num">1.3.1&nbsp;&nbsp;</span>Generate Suggestions</a></span></li><li><span><a href="#Test-STBO" data-toc-modified-id="Test-STBO-1.3.2"><span class="toc-item-num">1.3.2&nbsp;&nbsp;</span>Test STBO</a></span></li></ul></li><li><span><a href="#LCM-Kernel" data-toc-modified-id="LCM-Kernel-1.4"><span class="toc-item-num">1.4&nbsp;&nbsp;</span>LCM Kernel</a></span></li></ul></li><li><span><a href="#Weighted-MTBO" data-toc-modified-id="Weighted-MTBO-2"><span class="toc-item-num">2&nbsp;&nbsp;</span>Weighted MTBO</a></span></li></ul></div>

# Optimization

From the menu above, select "Runtime" -> "Run All".

If you've already run this noteboook recently, click on "Single Task Optimization", then click "Runtime" -> "Run After."

## Setup

In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
# path to multitask folder

import sys
# insert at 1, 0 is the script path (or '' in REPL)
sys.path.insert(1, '/Users/dsw46/Library/CloudStorage/OneDrive-UniversityofCambridge/Cambridge/Projects/MTBO/multitask')

In [3]:
from summit import *
from multitask import *
import pandas as pd
import torch
import gpytorch
import hiplot as hip

## Single Task Optimization A

Import data

In [30]:
df = pd.read_csv("../data/experiments/ch_activation_experiments_a.csv", skiprows=1)

In [31]:
num_experiments = 1

### Generate Suggestions

In [32]:
# Transform data
categorical_columns = ["Solvent", "Ligand"]
for col in categorical_columns:
    df[col] = df[col].str.split(r" \(\d\)", expand=True)[0]
for col in df.columns:
    if "Unnamed" in col:
        df = df.drop(col, axis=1)
df = df.rename(columns={"ResT /min": "ResT", "Temp /°C": "Temp", "Mol%": "Mol", "Yield /%": "yld"} )
ds  = DataSet.from_df(df)
ds

NAME                                       Data file          Type  Solvent  \
TYPE                                            DATA          DATA     DATA   
0                                    TrainingData001      Training     DMSO   
1                                    TrainingData002      Training     DMSO   
2                                    TrainingData003      Training  Toluene   
3                                    TrainingData004      Training      DMA   
4                                    TrainingData005      Training     MeCN   
5                                    TrainingData006      Training     MeCN   
6                                    TrainingData007      Training      NMP   
7                                    TrainingData008      Training     DMSO   
8                                    TrainingData009      Training      NMP   
9                                                NaN      Training      NMP   
10                                   TrainingData011      Training  Toluene   
11                                   TrainingData012      Training     MeCN   
12                                   TrainingData013      Training      DMA   
13                                   TrainingData014      Training      DMA   
14                                   TrainingData015      Training     DMSO   
15                                               NaN      Training  Toluene   
16                                               NaN  Optimization      NMP   
17                                               NaN  Optimization     MeCN   
18                                               NaN  Optimization  Toluene   
19    Bumped up to 100 restarts and 2000 raw samples  Optimization      NMP   
20                                               NaN  Optimization      NMP   
21                                               NaN  Optimization      NMP   
22                                               NaN  Optimization      NMP   

NAME    Ligand ResT Temp  Mol    yld    SM area Product area  ... Volume /mL  \
TYPE      DATA DATA DATA DATA   DATA       DATA         DATA  ...       DATA   
0      DPEPhos   60  140   10  46.09        NaN    3591526.0  ...        5.0   
1     JohnPhos   45   70    3   1.31  2704169.0     260938.0  ...        5.0   
2      DPEPhos   42   61    8    0.0        NaN          NaN  ...        5.0   
3     JohnPhos    9  135    5  37.91  1333228.0    4837572.0  ...        5.0   
4     JohnPhos   11  134    2  16.87  1614954.0    2408002.0  ...        5.0   
5     JohnPhos   19   80    5   69.7   723374.0   16037972.0  ...        5.0   
6     JohnPhos   47  143    4  40.92        NaN    7980309.0  ...        5.0   
7        SPhos   29  122    4    0.0  1001820.0          0.0  ...        5.0   
8        Xphos   52  112    8  55.69   647744.0   10707780.0  ...        5.0   
9      DPEPhos   26   53    6    0.0        NaN          NaN  ...        5.0   
10       Xphos    6   83    3   3.01  3037966.0     565891.0  ...        5.0   
11       Xphos   39   90    9   6.33  2462821.0    1180830.0  ...        5.0   
12       Xphos   51  104    9  16.11  1205010.0    3186820.0  ...        5.0   
13     DPEPhos   22   67    4   4.04  2696188.0     825115.0  ...        5.0   
14       Xphos   33  115    7    0.0        NaN          NaN  ...        5.0   
15       SPhos   19   57    8    0.0        NaN          NaN  ...        5.0   
16       Xphos   60  102   10   56.2        NaN          NaN  ...        NaN   
17    JohnPhos   20   69    6    5.9        NaN          NaN  ...        NaN   
18    JohnPhos   53  141    8   26.4        NaN          NaN  ...        NaN   
19       Xphos   60  123    9   42.4        NaN          NaN  ...        NaN   
20       Xphos   53   89    9   74.7        NaN          NaN  ...        NaN   
21       Xphos   46   88    9   46.0        NaN          NaN  ...        NaN   
22       Xphos   60   85    8   72.4        NaN          NaN  ...        NaN   

NAME Conc SM /M Mol% ca

In [33]:
# Create domain
domain = Domain()

# Solvents: Toluene (1), DMA (2), MeCN (3), DMSO (4), NMP (5)
# Ligand: JohnPhos (1), Sphos (2), Xphos (3), DPEPhos (4)
# ResT: 5 - 60 mins
# Temp: 50 - 150 deg
# Mol%: 2 - 10 %
domain += CategoricalVariable(
    "Solvent",
    "Solvent used for the reaction", 
    levels=["Toluene", "DMA", "MeCN", "DMSO", "NMP"]
)
domain += CategoricalVariable(
    "Ligand",
    "Ligand used for the reaction",
    levels=["JohnPhos", "SPhos", "Xphos", "DPEPhos"]
)
domain += ContinuousVariable(
    "ResT",
    "Residence Time (minutes)",
    bounds=(5, 60)
)
domain += ContinuousVariable(
    "Temp",
    "Reaction temperature in deg C",
    bounds=(50,150)
)
domain += ContinuousVariable(
    "Mol",
    "Catalyst mol percent",
    bounds=(2,10)
)
domain += ContinuousVariable(
    "yld",
    "Reaction yield",
    bounds=(0, 100),
    is_objective=True,
    maximize=True
)
print("Domain")
domain

Domain


In [34]:
cat_mappings = {}
cat_dimensions = []
for i, v in enumerate(domain.input_variables):
    if v.variable_type == "categorical":
        cat_mapping = {l: i for i, l in enumerate(v.levels)}
        cat_mappings[v.name] = cat_mapping
        cat_dimensions.append(i)

In [35]:
combos = domain.get_categorical_combinations()
for v in domain.input_variables:
    if v.variable_type == "categorical":
        combos[v.name] = combos[v.name].replace(cat_mappings[v.name])

In [36]:
strategy = NewSTBO(domain, acquisition_function="qNEI", categorical_method=None, brute_force_categorical=True)
suggestions = strategy.suggest_experiments(int(num_experiments), prev_res=ds)
suggestions = suggestions.round(0)
suggestions

NAME Solvent    Ligand  ResT  Temp  Mol strategy
TYPE    DATA      DATA  DATA  DATA DATA METADATA
0       MeCN  JohnPhos  57.0  80.0  9.0     STBO

In [37]:
from botorch.optim import optimize_acqf, optimize_acqf_mixed
inputs, output = strategy.transform.transform_inputs_outputs(
    ds,
    categorical_method=None,
    # standardize_inputs=True,
    min_max_scale_inputs=True,
    min_max_scale_outputs=True
    # standardize_outputs=True,
)
cat_mappings = {}
cat_dimensions = []
for i, v in enumerate(strategy.domain.input_variables):
    if v.variable_type == "categorical":
        cat_mapping = {l: i for i, l in enumerate(v.levels)}
        inputs[v.name] = inputs[v.name].replace(cat_mapping)
        cat_mappings[v.name] = cat_mapping
        cat_dimensions.append(i)
fixed_features_list = []
for k, combo in combos.iterrows():
    fixed_features_list.append(
        {dim: combo[i] for i, dim in enumerate(cat_dimensions)}
    )

ff_candidate_list, ff_acq_value_list = [], []
for fixed_features in fixed_features_list:
    candidate, acq_value = optimize_acqf(
        acq_function=strategy.acq,
        bounds=strategy._get_bounds(),
        q=1,
        num_restarts=100,
        raw_samples=2000,
        fixed_features=fixed_features,
        return_best_only=False,
    )
    ff_candidate_list.append(candidate)
    ff_acq_value_list.append(acq_value)
    
ff_candidate_list = torch.cat(ff_candidate_list)
# ff_acq_values = torch.stack(ff_acq_value_list)
X = pd.DataFrame(
    ff_candidate_list.squeeze().numpy(), 
    columns=[v.name for v in strategy.domain.input_variables]
)
X = DataSet.from_df(X)


for i, v in enumerate(strategy.domain.input_variables):
    if v.variable_type == "categorical":
        cat_mapping = {i: l for i, l in enumerate(v.levels)}
        X[v.name] = X[v.name].replace(cat_mapping)

X = strategy.transform.un_transform(
    X,
    categorical_method=None,
    min_max_scale_inputs=True,
    min_max_scale_outputs=True,
)
X = pd.DataFrame(
    X.values,
    columns=[v.name for v in strategy.domain.input_variables]
)
with torch.no_grad():
    acq = strategy.acq(ff_candidate_list)
X["acq"] = acq

with torch.no_grad():
    posterior = strategy.model.posterior(ff_candidate_list)
    samples = [posterior.sample() for i in range(100)]

samples = torch.stack(samples).squeeze()
avg = samples.mean(axis=0)
std = samples.std(axis=0)

X["y_mean"] = avg
X["y_std"] = std

In [38]:
import hiplot as hip
hexp = hip.Experiment.from_dataframe(X.sort_values("acq", ascending=False))
hexp.display_data(hip.Displays.PARALLEL_PLOT).update({"hide":["uid"]})
hexp.display()

<IPython.core.display.Javascript object>

In [39]:
strategy = NewSTBO(domain)
suggestions = strategy.suggest_experiments(int(num_experiments), prev_res=ds)
suggestions = suggestions.round(0)
suggestions

/Users/dsw46/opt/anaconda3/envs/dswigh_default/lib/python3.9/site-packages/summit/strategies/base.py:162: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  new_ds = new_ds.drop(variable.name, axis=1)
/Users/dsw46/opt/anaconda3/envs/dswigh_default/lib/python3.9/site-packages/summit/strategies/base.py:162: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  new_ds = new_ds.drop(variable.name, axis=1)
/Users/dsw46/opt/anaconda3/envs/dswigh_default/lib/python3.9/site-packages/summit/strategies/base.py:334: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  new_ds = new_ds.drop(one_hot_names, axis=1)
/Users/dsw46/opt/anaconda3/envs/dswigh_default/lib/python3.9/site-packages/summit/strategies/base.py:334: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance

NAME  ResT  Temp  Mol Solvent Ligand strategy
TYPE  DATA  DATA DATA    DATA   DATA METADATA
0     60.0  83.0  9.0     NMP  Xphos     STBO

In [40]:
from botorch.optim import optimize_acqf, optimize_acqf_mixed
inputs, output = strategy.transform.transform_inputs_outputs(
    ds,
    categorical_method="one-hot",
    # standardize_inputs=True,
    min_max_scale_inputs=True,
    min_max_scale_outputs=True
    # standardize_outputs=True,
)
candidates, acq_values= optimize_acqf(
    acq_function=strategy.acq,
    bounds=strategy._get_bounds(),
    num_restarts=100,
    q=1,
    raw_samples=2000,
    return_best_only=False
)

res = DataSet(candidates.squeeze(), columns=inputs.data_columns)
X = strategy.transform.un_transform(
    res,
    categorical_method="one-hot",
    min_max_scale_inputs=True,
    min_max_scale_outputs=True,
)

X = pd.DataFrame(
    X.values,
    columns=X.data_columns
)
with torch.no_grad():
    acq = strategy.acq(candidates)
X["acq"] = acq

with torch.no_grad():
    posterior = strategy.model.posterior(candidates)
    samples = [posterior.sample() for i in range(100)]

samples = torch.stack(samples).squeeze()
avg = samples.mean(axis=0)
std = samples.std(axis=0)

X["y_mean"] = avg
X["y_std"] = std

/Users/dsw46/opt/anaconda3/envs/dswigh_default/lib/python3.9/site-packages/summit/strategies/base.py:162: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  new_ds = new_ds.drop(variable.name, axis=1)
/Users/dsw46/opt/anaconda3/envs/dswigh_default/lib/python3.9/site-packages/summit/strategies/base.py:162: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  new_ds = new_ds.drop(variable.name, axis=1)
/Users/dsw46/opt/anaconda3/envs/dswigh_default/lib/python3.9/site-packages/summit/strategies/base.py:334: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  new_ds = new_ds.drop(one_hot_names, axis=1)
/Users/dsw46/opt/anaconda3/envs/dswigh_default/lib/python3.9/site-packages/summit/strategies/base.py:334: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance

In [41]:
import hiplot as hip
hexp = hip.Experiment.from_dataframe(X.sort_values("acq", ascending=False))
hexp.display_data(hip.Displays.PARALLEL_PLOT).update({"hide":["uid"]})
hexp.display()

<IPython.core.display.Javascript object>

In [42]:
strategy.model.covar_module.base_kernel.lengthscale

tensor([[0.3344, 0.3346, 0.3328, 0.3313, 0.3313, 0.3340, 0.3347, 0.3339, 0.3321,
         0.3596, 0.3410, 0.3233]], dtype=torch.float64,
       grad_fn=<SoftplusBackward0>)

## Multitask Experiments B

In [4]:
df_a = pd.read_csv("../data/experiments/ch_activation_experiments_a.csv", skiprows=1)
df_b = pd.read_csv("../data/experiments/ch_activation_experiments_b.csv", skiprows=1)

In [5]:
num_experiments = 1

In [12]:
df_a

Data file          Type      Solvent  \
0                                  TrainingData001      Training     DMSO (4)   
1                                  TrainingData002      Training     DMSO (4)   
2                                  TrainingData003      Training  Toluene (1)   
3                                  TrainingData004      Training      DMA (2)   
4                                  TrainingData005      Training     MeCN (3)   
5                                  TrainingData006      Training     MeCN (3)   
6                                  TrainingData007      Training      NMP (5)   
7                                  TrainingData008      Training     DMSO (4)   
8                                  TrainingData009      Training      NMP (5)   
9                                              NaN      Training      NMP (5)   
10                                 TrainingData011      Training  Toluene (1)   
11                                 TrainingData012      Training     MeCN (3)   
12                                 TrainingData013      Training      DMA (2)   
13                                 TrainingData014      Training      DMA (2)   
14                                 TrainingData015      Training     DMSO (4)   
15                                             NaN      Training  Toluene (1)   
16                                             NaN  Optimization      NMP (5)   
17                                             NaN  Optimization     MeCN (3)   
18                                             NaN  Optimization  Toluene (1)   
19  Bumped up to 100 restarts and 2000 raw samples  Optimization      NMP (5)   
20                                             NaN  Optimization      NMP (5)   
21                                             NaN  Optimization      NMP (5)   
22                                             NaN  Optimization      NMP (5)   

          Ligand  ResT /min  Temp /°C  Mol%  Yield /%    SM area  \
0    DPEPhos (4)         60       140    10     46.09        NaN   
1   JohnPhos (1)         45        70     3      1.31  2704169.0   
2    DPEPhos (4)         42        61     8      0.00        NaN   
3   JohnPhos (1)          9       135     5     37.91  1333228.0   
4   JohnPhos (1)         11       134     2     16.87  1614954.0   
5   JohnPhos (1)         19        80     5     69.70   723374.0   
6   JohnPhos (1)         47       143     4     40.92        NaN   
7      SPhos (2)         29       122     4      0.00  1001820.0   
8      Xphos (3)         52       112     8     55.69   647744.0   
9    DPEPhos (4)         26        53     6      0.00        NaN   
10     Xphos (3)          6        83     3      3.01  3037966.0   
11     Xphos (3)         39        90     9      6.33  2462821.0   
12     Xphos (3)         51       104     9     16.11  1205010.0   
13   DPEPhos (4)         22        67     4      4.04  2696188.0   
14     Xphos (3)         33       115     7      0.00        NaN   
15     SPhos (2)         19        57     8      0.00        NaN   
16     Xphos (3)         60       102    10     56.20        NaN   
17  JohnPhos (1)         20        69     6      5.90        NaN   
18  JohnPhos (1)         53       141     8     26.40        NaN   
19     Xphos (3)         60       123     9     42.40        NaN   
20     Xphos (3)         53        89     9     74.70        NaN   
21     Xphos (3)         46        88     9     46.00        NaN   
22     Xphos (3)         60        85     8     72.40        NaN   

    Product area  ...  Volume /mL Conc SM /M Mol% catalyst   SM /g  \
0      3591526.0  ...         5.0        0.1          10.0  0.1008   
1       260938.0  ...         5.0        0.1           3.0  0.1008   
2            NaN  ...         5.0        0.1           8.0  0.1008   
3      4837572.0  ...         5.0        0.1           5.0  0.1008   
4      2408002.0  ...         5.0        0.1           2.0  0.1008   
5     16037972.0  ...         5.0        0.

### Generate Suggestions

In [6]:
# Transform data
def transform_data(df):
    categorical_columns = ["Solvent", "Ligand"]
    for col in categorical_columns:
        df[col] = df[col].str.split(r" \(\d\)", expand=True)[0]
    for col in df.columns:
        if "Unnamed" in col:
            df = df.drop(col, axis=1)
    df = df.rename(columns={"ResT /min": "ResT", "Temp /°C": "Temp", "Mol%": "Mol", "Yield /%": "yld"} )
    ds  = DataSet.from_df(df)
    return ds

ds_a = transform_data(df_a)
ds_b = transform_data(df_b)
ds_a[("task", "METADATA")] = 0
ds_b[("task", "METADATA")] = 1

In [7]:
# Create domain
domain = Domain()

# Solvents: Toluene (1), DMA (2), MeCN (3), DMSO (4), NMP (5)
# Ligand: JohnPhos (1), Sphos (2), Xphos (3), DPEPhos (4)
# ResT: 5 - 60 mins
# Temp: 50 - 150 deg
# Mol%: 2 - 10 %
domain += CategoricalVariable(
    "Solvent",
    "Solvent used for the reaction", 
    levels=["Toluene", "DMA", "MeCN", "DMSO", "NMP"]
)
domain += CategoricalVariable(
    "Ligand",
    "Ligand used for the reaction",
    levels=["JohnPhos", "SPhos", "Xphos", "DPEPhos"]
)
domain += ContinuousVariable(
    "ResT",
    "Residence Time (minutes)",
    bounds=(5, 60)
)
domain += ContinuousVariable(
    "Temp",
    "Reaction temperature in deg C",
    bounds=(50,150)
)
domain += ContinuousVariable(
    "Mol",
    "Catalyst mol percent",
    bounds=(2,10)
)
domain += ContinuousVariable(
    "yld",
    "Reaction yield",
    bounds=(0, 100),
    is_objective=True,
    maximize=True
)
print("Domain")
domain

Domain


In [8]:
ds_b = ds_b.drop([7,8], axis=0)

In [23]:
strategy = NewMTBO(
    domain,
    pretraining_data=ds_a, 
    acquisition_function="qNEI",
    brute_force_categorical=True,
#     model_type=NewMTBO.LCM,
)

# tempor
suggestions = strategy.suggest_experiments(int(num_experiments), prev_res=ds_b)
suggestions = suggestions.round(0)
suggestions

/Users/dsw46/Library/CloudStorage/OneDrive-UniversityofCambridge/Cambridge/Projects/MTBO/multitask/multitask/mt.py:169: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  data = self.all_experiments.append(self.pretraining_data)
/Users/dsw46/opt/anaconda3/envs/dswigh_default/lib/python3.9/site-packages/summit/strategies/base.py:162: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  new_ds = new_ds.drop(variable.name, axis=1)
/Users/dsw46/opt/anaconda3/envs/dswigh_default/lib/python3.9/site-packages/summit/strategies/base.py:162: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  new_ds = new_ds.drop(variable.name, axis=1)
/Users/dsw46/opt/anaconda3/envs/dswigh_default/lib/python3.9/site-packages/sklearn/utils/validation.py:1688: FutureWarning: Feature names only support names that a

NAME  ResT  Temp  Mol Solvent    Ligand strategy     task
TYPE  DATA  DATA DATA    DATA      DATA METADATA METADATA
0     22.0  97.0  5.0    MeCN  JohnPhos     MTBO        1

In [24]:
from botorch.optim import optimize_acqf
from botorch.acquisition.acquisition import AcquisitionFunction
from torch import Tensor
from typing import List, Dict, Optional, Callable, Any

def optimize_acqf_mixed(
    acq_function: AcquisitionFunction,
    bounds: Tensor,
    q: int,
    num_restarts: int,
    fixed_features_list: List[Dict[int, float]],
    raw_samples: Optional[int] = None,
    options: Optional[Dict[str, Union[bool, float, int, str]]] = None,
    inequality_constraints: Optional[List[Tuple[Tensor, Tensor, float]]] = None,
    equality_constraints: Optional[List[Tuple[Tensor, Tensor, float]]] = None,
    post_processing_func: Optional[Callable[[Tensor], Tensor]] = None,
    batch_initial_conditions: Optional[Tensor] = None,
    **kwargs: Any,
) -> Tuple[Tensor, Tensor]:
    if q == 1:
        ff_candidate_list, ff_acq_value_list = [], []
        for fixed_features in fixed_features_list:
            candidate, acq_value = optimize_acqf(
                acq_function=acq_function,
                bounds=bounds,
                q=q,
                num_restarts=num_restarts,
                raw_samples=raw_samples,
                options=options or {},
                inequality_constraints=inequality_constraints,
                equality_constraints=equality_constraints,
                fixed_features=fixed_features,
                post_processing_func=post_processing_func,
                batch_initial_conditions=batch_initial_conditions,
                return_best_only=False,
            )
            ff_candidate_list.append(candidate)
            ff_acq_value_list.append(acq_value)

        ff_acq_values = torch.cat(ff_acq_value_list)
        best = torch.argmax(ff_acq_values)
        return ff_candidate_list, ff_acq_values


In [25]:
# from botorch.optim import optimize_acqf, optimize_acqf_mixed
inputs, output = strategy.transform.transform_inputs_outputs(
    ds_a.append(ds_b),
    categorical_method="one-hot",
    min_max_scale_inputs=True,
    min_max_scale_outputs=True
)
fixed_features_list = strategy._get_fixed_features()
candidates, acq_values= optimize_acqf_mixed(
    acq_function=strategy.acq,
    bounds=strategy._get_bounds(),
    fixed_features_list=fixed_features_list,
    num_restarts=100,
    q=1,
    raw_samples=2000,
    return_best_only=False
)


/var/folders/hm/0prtzp050kxc67zzx_zttjvh0000gp/T/ipykernel_31547/2596016044.py:3: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  ds_a.append(ds_b),
/Users/dsw46/opt/anaconda3/envs/dswigh_default/lib/python3.9/site-packages/summit/strategies/base.py:162: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  new_ds = new_ds.drop(variable.name, axis=1)
/Users/dsw46/opt/anaconda3/envs/dswigh_default/lib/python3.9/site-packages/summit/strategies/base.py:162: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  new_ds = new_ds.drop(variable.name, axis=1)
/Users/dsw46/opt/anaconda3/envs/dswigh_default/lib/python3.9/site-packages/sklearn/utils/validation.py:1688: FutureWarning: Feature names only support names that are all strings. Got feature names with dtypes: ['tuple']. An error will be ra

In [26]:
candidates_stacked = torch.cat([c.squeeze() for c in candidates])

In [27]:
res = DataSet(candidates_stacked, columns=inputs.data_columns)
X = strategy.transform.un_transform(
    res,
    categorical_method="one-hot",
    min_max_scale_inputs=True,
    min_max_scale_outputs=True
)

X = pd.DataFrame(
    X.values,
    columns=X.data_columns
)
# with torch.no_grad():
#     acq = strategy.acq(candidates)
X["acq"] = acq_values

with torch.no_grad():
    posterior = strategy.model.posterior(candidates_stacked)
    samples = [posterior.sample() for i in range(100)]

samples = torch.stack(samples).squeeze()
avg = samples.mean(axis=0)
std = samples.std(axis=0)

X["y_mean"] = avg
X["y_std"] = std

/Users/dsw46/opt/anaconda3/envs/dswigh_default/lib/python3.9/site-packages/summit/strategies/base.py:334: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  new_ds = new_ds.drop(one_hot_names, axis=1)
/Users/dsw46/opt/anaconda3/envs/dswigh_default/lib/python3.9/site-packages/summit/strategies/base.py:334: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  new_ds = new_ds.drop(one_hot_names, axis=1)
/Users/dsw46/opt/anaconda3/envs/dswigh_default/lib/python3.9/site-packages/gpytorch/utils/cholesky.py:38: NumericalWarning: A not p.d., added jitter of 1.0e-08 to the diagonal
  warnings.warn(


In [28]:
hexp = hip.Experiment.from_dataframe(X.sort_values("acq", ascending=False))
hexp.display_data(hip.Displays.PARALLEL_PLOT).update({"hide":["uid"]})
hexp.display()

<IPython.core.display.Javascript object>

In [29]:
strategy.model.covar_module.base_kernel.lengthscale

tensor([[0.3341, 0.3357, 0.3335, 0.3300, 0.3324, 0.3334, 0.3348, 0.3335, 0.3323,
         0.3652, 0.3811, 0.1933]], dtype=torch.float64,
       grad_fn=<SoftplusBackward0>)

### Test STBO

In [7]:
strategy = NewSTBO(
    domain,
    acquisition_function="qNEI",
    brute_force_categorical=True
)

suggestions = strategy.suggest_experiments(int(num_experiments), prev_res=ds_b)
suggestions = suggestions.round(0)
suggestions

/Users/Kobi/Library/Caches/pypoetry/virtualenvs/multitask-k0YbXS9f-py3.9/lib/python3.9/site-packages/summit/strategies/base.py:162: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  new_ds = new_ds.drop(variable.name, axis=1)
/Users/Kobi/Library/Caches/pypoetry/virtualenvs/multitask-k0YbXS9f-py3.9/lib/python3.9/site-packages/summit/strategies/base.py:162: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  new_ds = new_ds.drop(variable.name, axis=1)
/Users/Kobi/Library/Caches/pypoetry/virtualenvs/multitask-k0YbXS9f-py3.9/lib/python3.9/site-packages/sklearn/utils/validation.py:1688: FutureWarning: Feature names only support names that are all strings. Got feature names with dtypes: ['tuple']. An error will be raised in 1.2.
  warnings.warn(
/Users/Kobi/Library/Caches/pypoetry/virtualenvs/multitask-k0YbXS9f-py3.9/lib/python3.9/site-packages/sklearn/utils/validation.py

NAME  ResT   Temp  Mol Solvent    Ligand strategy
TYPE  DATA   DATA DATA    DATA      DATA METADATA
0     28.0  102.0  7.0    MeCN  JohnPhos     STBO

In [8]:
from botorch.optim import optimize_acqf
from botorch.acquisition.acquisition import AcquisitionFunction
from torch import Tensor
from typing import List, Dict, Optional, Callable, Any

def optimize_acqf_mixed(
    acq_function: AcquisitionFunction,
    bounds: Tensor,
    q: int,
    num_restarts: int,
    fixed_features_list: List[Dict[int, float]],
    raw_samples: Optional[int] = None,
    options: Optional[Dict[str, Union[bool, float, int, str]]] = None,
    inequality_constraints: Optional[List[Tuple[Tensor, Tensor, float]]] = None,
    equality_constraints: Optional[List[Tuple[Tensor, Tensor, float]]] = None,
    post_processing_func: Optional[Callable[[Tensor], Tensor]] = None,
    batch_initial_conditions: Optional[Tensor] = None,
    **kwargs: Any,
) -> Tuple[Tensor, Tensor]:
    if q == 1:
        ff_candidate_list, ff_acq_value_list = [], []
        for fixed_features in fixed_features_list:
            candidate, acq_value = optimize_acqf(
                acq_function=acq_function,
                bounds=bounds,
                q=q,
                num_restarts=num_restarts,
                raw_samples=raw_samples,
                options=options or {},
                inequality_constraints=inequality_constraints,
                equality_constraints=equality_constraints,
                fixed_features=fixed_features,
                post_processing_func=post_processing_func,
                batch_initial_conditions=batch_initial_conditions,
                return_best_only=False,
            )
            ff_candidate_list.append(candidate)
            ff_acq_value_list.append(acq_value)

        ff_acq_values = torch.cat(ff_acq_value_list)
        best = torch.argmax(ff_acq_values)
        return ff_candidate_list, ff_acq_values

In [9]:
# from botorch.optim import optimize_acqf, optimize_acqf_mixed
inputs, output = strategy.transform.transform_inputs_outputs(
    ds_b,
    categorical_method="one-hot",
    min_max_scale_inputs=True,
    min_max_scale_outputs=True
)
fixed_features_list = strategy._get_fixed_features()
candidates, acq_values= optimize_acqf_mixed(
    acq_function=strategy.acq,
    bounds=strategy._get_bounds(),
    fixed_features_list=fixed_features_list,
    num_restarts=100,
    q=1,
    raw_samples=2000,
    return_best_only=False
)

/Users/Kobi/Library/Caches/pypoetry/virtualenvs/multitask-k0YbXS9f-py3.9/lib/python3.9/site-packages/summit/strategies/base.py:162: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  new_ds = new_ds.drop(variable.name, axis=1)
/Users/Kobi/Library/Caches/pypoetry/virtualenvs/multitask-k0YbXS9f-py3.9/lib/python3.9/site-packages/summit/strategies/base.py:162: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  new_ds = new_ds.drop(variable.name, axis=1)
/Users/Kobi/Library/Caches/pypoetry/virtualenvs/multitask-k0YbXS9f-py3.9/lib/python3.9/site-packages/sklearn/utils/validation.py:1688: FutureWarning: Feature names only support names that are all strings. Got feature names with dtypes: ['tuple']. An error will be raised in 1.2.
  warnings.warn(
/Users/Kobi/Library/Caches/pypoetry/virtualenvs/multitask-k0YbXS9f-py3.9/lib/python3.9/site-packages/sklearn/utils/validation.py

In [11]:
candidates_stacked = torch.cat([c.squeeze() for c in candidates])

In [12]:
res = DataSet(candidates_stacked, columns=inputs.data_columns)
X = strategy.transform.un_transform(
    res,
    categorical_method="one-hot",
    min_max_scale_inputs=True,
    min_max_scale_outputs=True
)

X = pd.DataFrame(
    X.values,
    columns=X.data_columns
)
X["acq"] = acq_values

with torch.no_grad():
    posterior = strategy.model.posterior(candidates_stacked)
    samples = [posterior.sample() for i in range(100)]

samples = torch.stack(samples).squeeze()
avg = samples.mean(axis=0)
std = samples.std(axis=0)

X["y_mean"] = avg
X["y_std"] = std

/Users/Kobi/Library/Caches/pypoetry/virtualenvs/multitask-k0YbXS9f-py3.9/lib/python3.9/site-packages/summit/strategies/base.py:334: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  new_ds = new_ds.drop(one_hot_names, axis=1)
/Users/Kobi/Library/Caches/pypoetry/virtualenvs/multitask-k0YbXS9f-py3.9/lib/python3.9/site-packages/summit/strategies/base.py:334: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  new_ds = new_ds.drop(one_hot_names, axis=1)
/Users/Kobi/Library/Caches/pypoetry/virtualenvs/multitask-k0YbXS9f-py3.9/lib/python3.9/site-packages/gpytorch/utils/cholesky.py:38: NumericalWarning: A not p.d., added jitter of 1.0e-08 to the diagonal
  warnings.warn(


In [13]:
hexp = hip.Experiment.from_dataframe(X.sort_values("acq", ascending=False))
hexp.display_data(hip.Displays.PARALLEL_PLOT).update({"hide":["uid"]})
hexp.display()

<IPython.core.display.Javascript object>

## LCM Kernel

In [22]:
from multitask.mixed_gp_regression import LCMMultitaskGP

# Weighted MTBO

In [25]:
strategy = NewMTBO(
    domain,
    pretraining_data=ds_a, 
    acquisition_function="WeightedEI",
    brute_force_categorical=True,
#     model_type=NewMTBO.LCM,
)

# tempor
suggestions = strategy.suggest_experiments(int(num_experiments), prev_res=ds_b)
suggestions = suggestions.round(0)
suggestions

/Users/dsw46/Library/CloudStorage/OneDrive-UniversityofCambridge/Cambridge/Projects/MTBO/multitask/multitask/mt.py:174: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  data = self.all_experiments.append(self.pretraining_data)
/Users/dsw46/opt/anaconda3/envs/dswigh_default/lib/python3.9/site-packages/summit/strategies/base.py:162: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  new_ds = new_ds.drop(variable.name, axis=1)
/Users/dsw46/opt/anaconda3/envs/dswigh_default/lib/python3.9/site-packages/summit/strategies/base.py:162: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  new_ds = new_ds.drop(variable.name, axis=1)
/Users/dsw46/opt/anaconda3/envs/dswigh_default/lib/python3.9/site-packages/sklearn/utils/validation.py:1688: FutureWarning: Feature names only support names that a

NAME  ResT  Temp  Mol Solvent    Ligand strategy     task
TYPE  DATA  DATA DATA    DATA      DATA METADATA METADATA
0     25.0  81.0  4.0    MeCN  JohnPhos     MTBO        1